In [1]:
import pandas as pd
import numpy as np
from datetime import datetime
import os
import random
from tqdm import tqdm

In [2]:
# 교차로정보
inter_info = pd.read_csv("inter_info.csv")
inter_info['group_no'] = 3
display(inter_info)
inter_info.to_csv('../inter_info.csv')

inter_no        inter_name  inter_lat  inter_lon  group_no
0       175    한솔삼거리(한솔마을3거리)   37.36857  127.11478         3
1       176           느티마을4단지   37.36724  127.11480         3
2       177     한솔6단지(정자동사무소)   37.36619  127.11480         3
3       178             신기4거리   37.36346  127.11480         3
4       201           느티마을4거리   37.36854  127.10984         3
5       202        느티마을 안촌유치원   37.36855  127.11241         3
6       206         상록마을 321동   37.36483  127.10981         3
7       210  상록4거리(상록마을입구4거리)   37.36347  127.10982         3
8       211           상록마을단일로   37.36346  127.11237         3

In [3]:
# 현시구성
phase_info = pd.read_csv("phase_info.csv")
phase_info.drop('flow_no', axis=1, inplace=True)
# display(phase_info)
mg = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='min_green_dur').fillna(0).astype(int)
y = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='yellow_dur').fillna(0).astype(int)
r = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='red_dur').fillna(0).astype(int)
max_phase_no = phase_info['phase_no'].max()
new_columns = [f'{col}{phase}{ring}' for col in ['mg', 'y', 'r'] for phase in range(1, max_phase_no + 1) for ring in ['A', 'B']]
phase_info = pd.concat([mg, y, r], axis=1)
phase_info.columns = new_columns
phase_info['main_phase'] = 2
phase_info['mg6A'] = phase_info['mg6B'] = phase_info['mg7A'] = phase_info['mg7B'] = phase_info['mg8A'] = phase_info['mg8B']= 0
phase_info['y6A'] = phase_info['y6B'] = phase_info['y7A'] = phase_info['y7B'] = phase_info['y8A'] = phase_info['y8B']= 0
phase_info['r6A'] = phase_info['r6B'] = phase_info['r7A'] = phase_info['r7B'] = phase_info['r8A'] = phase_info['r8B']= 0
phase_info = phase_info[sorted(phase_info.columns)]
phase_info.reset_index(inplace=True)
with pd.option_context('display.max_rows', None, 'display.max_columns', None): 
    display(phase_info)
phase_info.to_csv('../phase_info.csv')

inter_no  main_phase  mg1A  mg1B  mg2A  mg2B  mg3A  mg3B  mg4A  mg4B  mg5A  \
0       175           2    24    27    33    12    15    39    15    19     0   
1       176           2    21    31    33    30    16     0     0     0     0   
2       177           2    35    18    36    36     0     0    38    13     0   
3       178           2    18    19    35    26    36    29    17    37     0   
4       201           2    25    20    21    32    31    28    31    17    27   
5       202           2    12    30     0     0     0     0     0     0     0   
6       206           2    36    29     0     0    31    31     0     0     0   
7       210           2    19     0    12    13    21    37    12    22     0   
8       211           2    32    35     0     0     0     0     0     0     0   

   mg5B  mg6A  mg6B  mg7A  mg7B  mg8A  mg8B  r1A  r1B  r2A  r2B  r3A  r3B  \
0     0     0     0     0     0     0     0    1    1    1    1    1    1   
1     0     0     0     0     0     0     0    1    1    1    1    1    0   
2     0     0     0     0     0     0     0    1    1    1    1    1    0   
3     0     0     0     0     0     0     0    1    1    1    1    1    1   
4    27     0     0     0     0     0     0    1    1    1    1    1    1   
5     0     0     0     0     0     0     0    1    1    1    0    0    0   
6     0     0     0     0     0     0     0    1    1    1    0    1    1   
7     0     0     0     0     0     0     0    1    0    1    1    1    1   
8     0     0     0     0     0     0     0    1    1    1    0    0    0   

   r4A  r4B  r5A  r5B  r6A  r6B  r7A  r7B  r8A  r8B  y1A  y1B  y2A  y2B  y3A  \
0    1    1    0    0    0    0    0    0    0    0    4    4    4    4    4   
1    0    0    0    0    0    0    0    0    0    0    4    4    4    4    4   
2    1    1    0    0    0    0    0    0    0    0    4    4    4    4    0   
3    1    1    0    0    0    0    0    0    0    0    4    4    4    4    4   
4    1    1    1    1    0    0    0    0    0    0    4    4    4    4    4   
5    0    0    0    0    0    0    0    0    0    0    4    4    0    0    0   
6    1    0    0    0    0    0    0    0    0    0    4    4    0    0    4   
7    1    1    0    0    0    0    0    0    0    0    4    0    4    4    4   
8    0    0    0    0    0    0    0    0    0    0    4    4    0    0    0   

   y3B  y4A  y4B  y5A  y5B  y6A  y6B  y7A  y7B  y8A  y8B  
0    4    4    4    0    0    0    0    0    0    0    0  
1    0    0    0    0    0    0    0    0    0    0    0  
2    0    4    4    0    0    0    0    0    0    0    0  
3    4    4    4    0    0    0    0    0    0    0    0  
4    4    4    4    4    4    0    0    0    0    0    0  
5    0    0    0    0    0    0    0    0    0    0    0  
6    4    0    0    0    0    0    0    0    0    0    0  
7    4    4    4    0    0    0    0    0    0    0    0  
8    0    0    0    0    0    0    0    0    0    0    0

In [4]:
# 방위각정보
flow_angle = pd.read_csv("flow_angle.csv")
angle = flow_angle.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='angle_code', aggfunc='first').fillna('NaN')
new_columns = [f'angle_{ring}{phase}' for phase in range(1, 6) for ring in ['A', 'B']]
angle.columns = new_columns
angle['angle_A6'] = angle['angle_A7'] = angle['angle_A8'] = np.nan
angle['angle_B6'] = angle['angle_B7'] = angle['angle_B8'] = np.nan
angle = angle[sorted(angle.columns)]
display(angle)
flow_angle.to_csv('../angle.csv')

angle_A1 angle_A2 angle_A3 angle_A4 angle_A5  angle_A6  angle_A7  \
inter_no                                                                    
175        179004     1095    90270   268000      NaN       NaN       NaN   
176        180000   180000   270356      NaN      NaN       NaN       NaN   
177        180000       90     stop   268000      NaN       NaN       NaN   
178        180000       90   270000    90270      NaN       NaN       NaN   
201        180000   270000    90270    90270       90       NaN       NaN   
202         90270     stop      NaN      NaN      NaN       NaN       NaN   
206        180000     stop   180000     stop      NaN       NaN       NaN   
210         90270   268000   359090   180000      NaN       NaN       NaN   
211         90270     stop      NaN      NaN      NaN       NaN       NaN   

          angle_A8 angle_B1 angle_B2 angle_B3 angle_B4 angle_B5  angle_B6  \
inter_no                                                                    
175            NaN     3176   179270    90180   270090      NaN       NaN   
176            NaN   359180   180270      NaN      NaN      NaN       NaN   
177            NaN     1176   179270      NaN    90180      NaN       NaN   
178            NaN      180   180270   270090    90180      NaN       NaN   
201            NaN   180270   270090   270090    90180      180       NaN   
202            NaN   270090      NaN      NaN      NaN      NaN       NaN   
206            NaN      180      NaN      180      NaN      NaN       NaN   
210            NaN      NaN   270090      180   180270      NaN       NaN   
211            NaN   270090      NaN      NaN      NaN      NaN       NaN   

          angle_B7  angle_B8  
inter_no                      
175            NaN       NaN  
176            NaN       NaN  
177            NaN       NaN  
178            NaN       NaN  
201            NaN       NaN  
202            NaN       NaN  
206            NaN       NaN  
210            NaN       NaN  
211            NaN       NaN

In [5]:
# # 이동류번호
# plan = pd.read_csv("time_plan.csv")
# phase = pd.read_csv('phase_info.csv')
# plan = plan[plan.ID.isin([1, 5, 8, 11])]
# ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
# plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
# plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
# plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration', 'cycle']]
# plan_ = pd.merge(plan, phase[['inter_no', 'phase_no', 'ring_type', 'flow_no']], on=['inter_no', 'phase_no', 'ring_type'], how='left')
# plan_['flow_no'] = plan_['flow_no'].fillna(18).astype(int)
# plan_['start_second'] = plan_.start_hour.astype(int)*3600 + plan_.start_minute.astype(int)*60
# plan_ = plan_[['inter_no', 'start_second', 'phase_no', 'ring_type', 'duration', 'flow_no', 'cycle']]
# cycle_dict = dict(zip(zip(plan_['inter_no'], plan_['start_second']), plan_['cycle']))
# df = plan_[['inter_no','start_second','cycle']].drop_duplicates()
# df = df.reset_index(drop=True)
# df['start_second_exact'] = 0
# for i in range(1, len(df)):
#     if i % 4 != 0:
#         prev = df.loc[i-1, 'start_second_exact']
#         start_second = df.loc[i, 'start_second']
#         cycle = df.loc[i-1, 'cycle']
#         df.loc[i, 'start_second_exact'] = (start_second - prev) % cycle + start_second
# inter2start = {inter_no:list(df[df.inter_no==inter_no]['start_second_exact']) for inter_no in df.inter_no}
# plan_ = plan_.pivot_table(index=['inter_no', 'start_second', 'phase_no'],
#                                 columns='ring_type',
#                                 values=['duration', 'flow_no'],
#                                 aggfunc='first').reset_index()
# plan_.columns = ['inter_no', 'start_second', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']
# inter2no_phase = {inter_no:group.phase_no.unique().max() for (inter_no, group) in plan.groupby('inter_no')}

# midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
# present = int(datetime(2024, 1, 5, 3, 3, 10).timestamp()) # <===== 현재시각
# sec = present - midnight
# the_start_second = np.max(df.start_second[df.start_second <= sec])
# move = []
# for inter_no in plan_.inter_no.unique():
#     cycle = cycle_dict[(inter_no, the_start_second)]
#     df = plan_[(plan_.inter_no==inter_no)&(plan_.start_second==the_start_second)].reset_index(drop=True)
#     remainder = sec % cycle
#     df['cums_A'] = df.copy().dura_A.cumsum()
#     df['cums_B'] = df.copy().dura_B.cumsum()
#     ind_A = len(df.cums_A[df.cums_A <= remainder])%inter2no_phase[inter_no]
#     ind_B = len(df.cums_B[df.cums_B <= remainder])%inter2no_phase[inter_no]
#     dura_A = df.loc[ind_A,'dura_A']
#     dura_B = df.loc[ind_B,'dura_B']
#     phas_A = df.loc[ind_A,'phase_no']
#     phas_B = df.loc[ind_B,'phase_no']
#     move_A = df.loc[ind_A,'move_A']
#     move_B = df.loc[ind_B,'move_B']
#     move.append(pd.DataFrame({'inter_no':[inter_no],'phas_A':[phas_A], 'phas_B':[phas_B],'move_A':[move_A], 'move_B':[move_B]}))
# move = pd.concat(move)
# display(move)
# move.to_csv('../movement.csv')

In [6]:
# 이동류번호
plan = pd.read_csv("time_plan.csv")
phase = pd.read_csv('phase_info.csv')
plan = plan[plan.ID.isin([1, 5, 8, 11])]
ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration', 'cycle']]
plan_ = pd.merge(plan, phase[['inter_no', 'phase_no', 'ring_type', 'flow_no']], on=['inter_no', 'phase_no', 'ring_type'], how='left')
plan_['flow_no'] = plan_['flow_no'].fillna(18).astype(int)
plan_['start_second'] = plan_.start_hour.astype(int)*3600 + plan_.start_minute.astype(int)*60
plan_ = plan_[['inter_no', 'start_second', 'phase_no', 'ring_type', 'duration', 'flow_no', 'cycle']]
cycle_dict = dict(zip(zip(plan_['inter_no'], plan_['start_second']), plan_['cycle']))
df = plan_[['inter_no','start_second','cycle']].drop_duplicates()
df = df.reset_index(drop=True)
df['start_second_exact'] = 0
for i in range(1, len(df)):
    if i % 4 != 0:
        prev = df.loc[i-1, 'start_second_exact']
        start_second = df.loc[i, 'start_second']
        cycle = df.loc[i-1, 'cycle']
        df.loc[i, 'start_second_exact'] = (start_second - prev) % cycle + start_second
inter2start = {inter_no:list(df[df.inter_no==inter_no]['start_second_exact']) for inter_no in df.inter_no}
plan_ = plan_.pivot_table(index=['inter_no', 'start_second', 'phase_no'],
                                columns='ring_type',
                                values=['duration', 'flow_no'],
                                aggfunc='first').reset_index()
plan_.columns = ['inter_no', 'start_second', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']
inter2no_phase = {inter_no:group.phase_no.unique().max() for (inter_no, group) in plan.groupby('inter_no')}

midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
for current_time in tqdm(range(midnight, next_day, 5)):
    sec = current_time - midnight
    the_start_second = np.max(df.start_second[df.start_second <= sec])
    move = []
    for inter_no in plan_.inter_no.unique():
        cycle = cycle_dict[(inter_no, the_start_second)]
        df = plan_[(plan_.inter_no==inter_no)&(plan_.start_second==the_start_second)].reset_index(drop=True)
        remainder = sec % cycle
        df['cums_A'] = df.copy().dura_A.cumsum()
        df['cums_B'] = df.copy().dura_B.cumsum()
        ind_A = len(df.cums_A[df.cums_A <= remainder])%inter2no_phase[inter_no]
        ind_B = len(df.cums_B[df.cums_B <= remainder])%inter2no_phase[inter_no]
        dura_A = df.loc[ind_A,'dura_A']
        dura_B = df.loc[ind_B,'dura_B']
        phas_A = df.loc[ind_A,'phase_no']
        phas_B = df.loc[ind_B,'phase_no']
        move_A = df.loc[ind_A,'move_A']
        move_B = df.loc[ind_B,'move_B']
        move.append(pd.DataFrame({'inter_no':[inter_no],'phas_A':[phas_A], 'phas_B':[phas_B],'move_A':[move_A], 'move_B':[move_B]}))
    move = pd.concat(move)
    move.to_csv(f'../moves/move_{current_time}.csv')

  0%|          | 0/17280 [00:00<?, ?it/s]

100%|██████████| 17280/17280 [04:37<00:00, 62.20it/s]


In [11]:
# 신호계획
plan = pd.read_csv("time_plan.csv")
plan = plan[plan.ID.isin([1, 5, 8, 11])]
ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration', 'cycle', 'offset']]
plan = plan.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'cycle', 'offset'], columns=['phase_no','ring_type'], values='duration', aggfunc='first').fillna(0).astype(int)
new_columns = [f'dura_{ring}{phase}' for phase in range(1, 6) for ring in ['A', 'B']]
plan.columns = new_columns
new_columns = [f'dura_{ring}{phase}' for phase in range(1, 9) for ring in ['A', 'B']]
for col in new_columns:
    if col not in plan.columns:
        plan[col] = 0
plan.reset_index(inplace=True)
plan = plan[list(plan.columns)[:3] + sorted(plan.columns)[1:-4] + list(plan.columns)[3:5]]
plan.to_csv('../plan.csv')
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(plan)
pland = plan.copy()
cums_A = np.array(pland[[f'dura_A{k}' for k in range(1,9)]].cumsum(axis=1))
cums_B = np.array(pland[[f'dura_B{k}' for k in range(1,9)]].cumsum(axis=1))
detailed_cums = []
i = 0
for row_A, row_B in zip(cums_A, cums_B):
    combined_row = np.unique(np.concatenate((row_A, row_B)))
    ddur = np.concatenate(([combined_row[0]], np.diff(combined_row)))
    ddur = np.pad(ddur, (0, 8 - len(ddur)), constant_values=(0))
    detailed_cums.append(ddur)
    for j in range(8):
        pland.at[i, f'ddur_{j+1}'] = ddur[j]
    i+=1
pland = pland[['inter_no', 'start_hour', 'start_minute'] + [f'ddur_{i}' for i in range(1,9)] + ['cycle', 'offset']
            #+ [f'dura_{phase}{i}' for phase in ['A','B'] for i in range(1,9)]
            ] # plan, detailed
pland[[f'ddur_{i}' for i in range(1,9)]] = pland[[f'ddur_{i}' for i in range(1,9)]].astype(int)
display(pland)

inter_no start_hour start_minute  dura_A1  dura_A2  dura_A3  dura_A4  \
0        175         00           00       37       39       55       29   
1        175         07           00       40       42       55       33   
2        175         09           00       43       45       55       37   
3        175         18           30       46       48       55       41   
4        176         00           00       37       73       40        0   
5        176         07           00       37       93       40        0   
6        176         09           00       37      103       40        0   
7        176         18           30       37      113       40        0   
8        177         00           00       36       20       68       26   
9        177         07           00       40       25       71       34   
10       177         09           00       43       27       70       40   
11       177         18           30       45       32       77       36   
12       178         00           00       38       39       40       23   
13       178         07           00       38       39       42       41   
14       178         09           00       38       39       43       50   
15       178         18           30       38       39       44       59   
16       201         00           00       24       24       17       58   
17       201         07           00       30       36       18       58   
18       201         09           00       33       36       25       58   
19       201         18           30       36       50       18       58   
20       202         00           00       39      101        0        0   
21       202         07           00       46      114        0        0   
22       202         09           00       46      114        0        0   
23       202         18           30       48      122        0        0   
24       206         00           00       33       35       26       26   
25       206         07           00       44       44       26       26   
26       206         09           00       45       53       26       26   
27       206         18           30       46       62       26       26   
28       210         00           00       43       29       56       22   
29       210         07           00       43       39       65       23   
30       210         09           00       43       43       70       24   
31       210         18           30       43       47       75       25   
32       211         00           00       28       97        0        0   
33       211         07           00       28      107        0        0   
34       211         09           00       28      112        0        0   
35       211         18           30       28      117        0        0   

    dura_A5  dura_A6  dura_A7  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  \
0         0        0        0        0       37       39       25       59   
1         0        0        0        0       40       42       29       59   
2         0        0        0        0       43       45       33       59   
3         0        0        0        0       46       48       37       59   
4         0        0        0        0       37       73       40        0   
5         0        0        0        0       37       93       40        0   
6         0        0        0        0       37      103       40        0   
7         0        0        0        0       37      113       40        0   
8         0        0        0        0       36       20       68       26   
9         0        0        0        0       40       25       71       34   
10        0        0        0        0       43       27       70       40   
11        0        0        0        0       45       32       77       36   
12        0        0        0        0       38       39       40       23   
13        0        0        0        0       38       39       62       21   
14        0        0 

inter_no start_hour start_minute  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  \
0        175         00           00      37      39      25      30      29   
1        175         07           00      40      42      29      26      33   
2        175         09           00      43      45      33      22      37   
3        175         18           30      46      48      37      18      41   
4        176         00           00      37      73      40       0       0   
5        176         07           00      37      93      40       0       0   
6        176         09           00      37     103      40       0       0   
7        176         18           30      37     113      40       0       0   
8        177         00           00      36      20      68      26       0   
9        177         07           00      40      25      71      34       0   
10       177         09           00      43      27      70      40       0   
11       177         18           30      45      32      77      36       0   
12       178         00           00      38      39      40      23       0   
13       178         07           00      38      39      42      20      21   
14       178         09           00      38      39      43      28      22   
15       178         18           30      38      39      44      36      23   
16       201         00           00      24      24      17      58      17   
17       201         07           00      30      36      18      58      18   
18       201         09           00      33      36      25      58      18   
19       201         18           30      36      50      18      58      18   
20       202         00           00      39     101       0       0       0   
21       202         07           00      46     114       0       0       0   
22       202         09           00      46     114       0       0       0   
23       202         18           30      48     122       0       0       0   
24       206         00           00      33      35      26      26       0   
25       206         07           00      44      44      26      26       0   
26       206         09           00      45      53      26      26       0   
27       206         18           30      46      62      26      26       0   
28       210         00           00      24      19      29      56      22   
29       210         07           00      24      19      39      65      23   
30       210         09           00      28      15      43      70      24   
31       210         18           30      24      19      47      75      25   
32       211         00           00      28      97       0       0       0   
33       211         07           00      28     107       0       0       0   
34       211         09           00      28     112       0       0       0   
35       211         18           30      28     117       0       0       0   

    ddur_6  ddur_7  ddur_8  cycle  offset  
0        0       0       0    160      57  
1        0       0       0    170      40  
2        0       0       0    180      28  
3        0       0       0    190      18  
4        0       0       0    150     131  
5        0       0       0    170     153  
6        0       0       0    180     169  
7        0       0       0    190     185  
8        0       0       0    150      35  
9        0       0       0    170      33  
10       0       0       0    180      41  
11       0       0       0    190      49  
12       0       0       0    140      50  
13       0       0       0    160      90  
14       0       0       0    170      80  
15       0       0       0    180      75  
16       0       0       0    140     133  
17       0       0       0    160     132  
18       0       0       0    170     134  
19       0       0       0    180     137  
20       0       0       0    140     103  
21       0       0       0    160     103  
22       0       0       0    1

In [8]:
# 신호이력
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
pland['end_unix'] = pland['start_hour'].astype(int)*3600 + plan['start_minute'].astype(int)*60 + midnight
history = []
for inter_no in pland.inter_no.unique():
    aplan = pland[pland.inter_no == inter_no]
    rows = []
    current_time = midnight
    for i in range(len(aplan)):
        first_row = aplan.iloc[i]
        cycle = first_row['cycle']
        unix_end = aplan.iloc[i+1]['end_unix'] if i < len(aplan) - 1 else next_day
        r = 0
        while current_time <= unix_end:
            remainder = current_time % 10
            if remainder != 0:
                r = (5 - remainder) % 10 - 5
            else:
                r = random.choices([0, -1, 1], weights=[10, 1, 1])[0]
            if random.random() < 0.005:
                n = random.randint(0,100)
                current_time += n * cycle + r
            elif random.random() > 0.995:
                n = random.randint(0,100)
                current_time += n * cycle + int(random.random() * cycle) + r
            else:
                current_time += cycle + r
            new_row = first_row.copy()
            new_row['end_unix'] = current_time
            rows.append(new_row)
    ahistory = pd.concat(rows, axis=1).transpose().reset_index(drop=True)
    history.append(ahistory)
history = pd.concat(history)
history = history[history.end_unix <= next_day]
history = history.sort_values(by='end_unix').reset_index(drop=True)
history.to_csv('../history.csv')
display(history[:30])

inter_no start_hour start_minute ddur_1 ddur_2 ddur_3 ddur_4 ddur_5 ddur_6  \
0       206         00           00     33     35     26     26      0      0   
1       211         00           00     28     97      0      0      0      0   
2       178         00           00     38     39     40     23      0      0   
3       201         00           00     24     24     17     58     17      0   
4       202         00           00     39    101      0      0      0      0   
5       176         00           00     37     73     40      0      0      0   
6       177         00           00     36     20     68     26      0      0   
7       210         00           00     24     19     29     56     22      0   
8       175         00           00     37     39     25     30     29      0   
9       206         00           00     33     35     26     26      0      0   
10      211         00           00     28     97      0      0      0      0   
11      202         00           00     39    101      0      0      0      0   
12      178         00           00     38     39     40     23      0      0   
13      201         00           00     24     24     17     58     17      0   
14      210         00           00     24     19     29     56     22      0   
15      176         00           00     37     73     40      0      0      0   
16      177         00           00     36     20     68     26      0      0   
17      175         00           00     37     39     25     30     29      0   
18      206         00           00     33     35     26     26      0      0   
19      211         00           00     28     97      0      0      0      0   
20      201         00           00     24     24     17     58     17      0   
21      178         00           00     38     39     40     23      0      0   
22      202         00           00     39    101      0      0      0      0   
23      176         00           00     37     73     40      0      0      0   
24      177         00           00     36     20     68     26      0      0   
25      210         00           00     24     19     29     56     22      0   
26      206         00           00     33     35     26     26      0      0   
27      175         00           00     37     39     25     30     29      0   
28      211         00           00     28     97      0      0      0      0   
29      178         00           00     38     39     40     23      0      0   

   ddur_7 ddur_8 cycle offset    end_unix  
0       0      0   120     10  1704380520  
1       0      0   125     45  1704380525  
2       0      0   140     50  1704380540  
3       0      0   140    133  1704380540  
4       0      0   140    103  1704380540  
5       0      0   150    131  1704380549  
6       0      0   150     35  1704380550  
7       0      0   150    115  1704380550  
8       0      0   160     57  1704380560  
9       0      0   120     10  1704380640  
10      0      0   125     45  1704380645  
11      0      0   140    103  1704380679  
12      0      0   140     50  1704380680  
13      0      0   140    133  1704380680  
14      0      0   150    115  1704380699  
15      0      0   150    131  1704380700  
16      0      0   150     35  1704380700  
17      0      0   160     57  1704380720  
18      0      0   120     10  1704380760  
19      0      0   125     45  1704380765  
20      0      0   140    133  1704380820  
21      0      0   140     50  1704380820  
22      0      0   140    103  1704380820  
23      0      0   150    131  1704380850  
24      0      0   150     35  1704380850  
25      0      0   150    115  1704380850  
26      0      0   120     10  1704380880  
27      0      0   160     57  1704380880  
28      0      0   125     45  1704380885  
29      0      0   140     50  1704380960

In [9]:
# 교차로-노드 매칭
uturn = pd.read_csv('U_TURN.csv')
inter_node = pd.read_csv('inter.csv')
inter_node = inter_node[['INT_NO', 'node_id', 'P/C']]
# inter_node.drop(index=len(inter_node) - 1, inplace=True)
inter_node.columns = ['inter_no', 'node_id', 'inter_type'] # parent : 주교차로, child : 부교차로
inter_node['inter_no'] = inter_node['inter_no'].astype(int) # i : intersection, u : u-turn intersection, c : coupling intersection
inter_node.iloc[-1] = pd.Series([211, 'c30', 'parent'])
inter_node.to_csv('../inter_node.csv')
display(inter_node)

inter_no node_id inter_type
0        175      i0     parent
1        175     u00      child
2        176      i1     parent
3        177      i2     parent
4        177     u20      child
5        178      i3     parent
6        178     u30      child
7        178     u31      child
8        178     u32      child
9        201      i8     parent
10       202      i9     parent
11       206      i7     parent
12       210      i6     parent
13       210     u60      child
14       211     c30     parent

In [10]:
# 부교차로 정보
# 지금은 생략 (23. 1. 9. 09:32)